In [1]:

import pandas as pd
import cv2
import numpy as np
from sklearn.model_selection import train_test_split

dataset_path = '/Users/navyarao/Downloads/challenges-in-representation-learning-facial-expression-recognition-challenge/fer2013/fer2013.csv'
image_size=(48,48)
 
def load_fer2013():
    data = pd.read_csv(dataset_path)
    pixels = data['pixels'].tolist()
    width, height = 48, 48
    faces = []
    for pixel_sequence in pixels:
        face = [int(pixel) for pixel in pixel_sequence.split(' ')]
        face = np.asarray(face).reshape(width, height)
        face = cv2.resize(face.astype('uint8'),image_size)
        faces.append(face.astype('float32'))
    faces = np.asarray(faces)
    faces = np.expand_dims(faces, -1)
    emotions = pd.get_dummies(data['emotion']).as_matrix()
    return faces, emotions
 
def preprocess_input(x, v2=True):
    x = x.astype('float32')
    x = x / 255.0
    if v2:
        x = x - 0.5
        x = x * 2.0
    return x
 
faces, emotions = load_fer2013()
faces = preprocess_input(faces)
xtrain, xtest,ytrain,ytest = train_test_split(faces, emotions,test_size=0.2,shuffle=True)

/Users/navyarao/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:22: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.


In [2]:
from keras.callbacks import CSVLogger, ModelCheckpoint, EarlyStopping
from keras.callbacks import ReduceLROnPlateau
from keras.preprocessing.image import ImageDataGenerator
from sklearn.model_selection import train_test_split
from keras.layers import Activation, Convolution2D, Dropout, Conv2D
from keras.layers import AveragePooling2D, BatchNormalization
from keras.layers import GlobalAveragePooling2D
from keras.models import Sequential
from keras.layers import Flatten
from keras.models import Model
from keras.layers import Input
from keras.layers import MaxPooling2D
from keras.layers import SeparableConv2D
from keras import layers
from keras.regularizers import l2
import pandas as pd
import cv2
import numpy as np


Using TensorFlow backend.


In [3]:
# parameters
batch_size = 32
num_epochs = 80
input_shape = (48, 48, 1)
verbose = 1
num_classes = 7
patience = 50
base_path = '/Users/navyarao/Downloads/FaceEmotion_ID-master/models/'
l2_regularization=0.01
 
# data generator
data_generator = ImageDataGenerator(
                        featurewise_center=False,
                        featurewise_std_normalization=False,
                        rotation_range=10,
                        width_shift_range=0.1,
                        height_shift_range=0.1,
                        zoom_range=.1,
                        horizontal_flip=True)
 
# model parameters
regularization = l2(l2_regularization)
 
# base
img_input = Input(input_shape)
x = Conv2D(8, (3, 3), strides=(1, 1), kernel_regularizer=regularization, use_bias=False)(img_input)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Conv2D(8, (3, 3), strides=(1, 1), kernel_regularizer=regularization, use_bias=False)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
 
# module 1
residual = Conv2D(16, (1, 1), strides=(2, 2), padding='same', use_bias=False)(x)
residual = BatchNormalization()(residual)
x = SeparableConv2D(16, (3, 3), padding='same', kernel_regularizer=regularization, use_bias=False)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = SeparableConv2D(16, (3, 3), padding='same', kernel_regularizer=regularization, use_bias=False)(x)
x = BatchNormalization()(x)
x = MaxPooling2D((3, 3), strides=(2, 2), padding='same')(x)
x = layers.add([x, residual])
 
# module 2
residual = Conv2D(32, (1, 1), strides=(2, 2), padding='same', use_bias=False)(x)
residual = BatchNormalization()(residual)
x = SeparableConv2D(32, (3, 3), padding='same', kernel_regularizer=regularization, use_bias=False)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = SeparableConv2D(32, (3, 3), padding='same', kernel_regularizer=regularization, use_bias=False)(x)
x = BatchNormalization()(x)
x = MaxPooling2D((3, 3), strides=(2, 2), padding='same')(x)
x = layers.add([x, residual])
 
# module 3
residual = Conv2D(64, (1, 1), strides=(2, 2),padding='same', use_bias=False)(x)
residual = BatchNormalization()(residual)
x = SeparableConv2D(64, (3, 3), padding='same',kernel_regularizer=regularization,use_bias=False)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = SeparableConv2D(64, (3, 3), padding='same',kernel_regularizer=regularization,use_bias=False)(x)
x = BatchNormalization()(x)
x = MaxPooling2D((3, 3), strides=(2, 2), padding='same')(x)
x = layers.add([x, residual])
 
# module 4
residual = Conv2D(128, (1, 1), strides=(2, 2),padding='same', use_bias=False)(x)
residual = BatchNormalization()(residual)
x = SeparableConv2D(128, (3, 3), padding='same',kernel_regularizer=regularization,use_bias=False)(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = SeparableConv2D(128, (3, 3), padding='same',kernel_regularizer=regularization,use_bias=False)(x)
x = BatchNormalization()(x)
x = MaxPooling2D((3, 3), strides=(2, 2), padding='same')(x)
x = layers.add([x, residual])
x = Conv2D(num_classes, (3, 3), padding='same')(x)
x = GlobalAveragePooling2D()(x)
output = Activation('softmax',name='predictions')(x)
 
model = Model(img_input, output)
model.compile(optimizer='adam', loss='categorical_crossentropy',metrics=['accuracy'])
model.summary()
 
# callbacks
#log_file_path = base_path + '_emotion_training.log'
#csv_logger = CSVLogger(log_file_path, append=False)
early_stop = EarlyStopping('val_loss', patience=patience)
reduce_lr = ReduceLROnPlateau('val_loss', factor=0.1, patience=int(patience/4), verbose=1)
trained_models_path = base_path + '_mini_XCEPTION'
model_names = trained_models_path + '.{epoch:02d}-{val_acc:.2f}.hdf5'
model_checkpoint = ModelCheckpoint(model_names, 'val_loss', verbose=1,save_best_only=True)
callbacks = [model_checkpoint, early_stop, reduce_lr]
 
model.fit_generator(data_generator.flow(xtrain, ytrain,batch_size),
                        steps_per_epoch=len(xtrain) / batch_size,
                        epochs=num_epochs, verbose=1, callbacks=callbacks,
                        validation_data=(xtest,ytest))

W0927 10:27:12.899737 140735715611520 deprecation_wrapper.py:119] From /Users/navyarao/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0927 10:27:12.917845 140735715611520 deprecation_wrapper.py:119] From /Users/navyarao/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0927 10:27:12.923109 140735715611520 deprecation_wrapper.py:119] From /Users/navyarao/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0927 10:27:12.945839 140735715611520 deprecation_wrapper.py:119] From /Users/navyarao/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:174: The name tf.get_default_session is deprecated. Please use tf.compat.v1.ge

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 48, 48, 1)    0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 46, 46, 8)    72          input_1[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, 46, 46, 8)    32          conv2d_1[0][0]                   
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 46, 46, 8)    0           batch_normalization_1[0][0]      
__________________________________________________________________________________________________
conv2d_2 (

Epoch 1/80
898/897 [==============================] - 143s 159ms/step - loss: 1.7683 - acc: 0.3309 - val_loss: 1.6548 - val_acc: 0.3855

Epoch 00001: val_loss improved from inf to 1.65483, saving model to /Users/navyarao/Downloads/FaceEmotion_ID-master/models/_mini_XCEPTION.01-0.39.hdf5
Epoch 2/80
898/897 [==============================] - 140s 156ms/step - loss: 1.5256 - acc: 0.4268 - val_loss: 1.4262 - val_acc: 0.4609

Epoch 00002: val_loss improved from 1.65483 to 1.42618, saving model to /Users/navyarao/Downloads/FaceEmotion_ID-master/models/_mini_XCEPTION.02-0.46.hdf5
Epoch 3/80
898/897 [==============================] - 140s 155ms/step - loss: 1.3992 - acc: 0.4743 - val_loss: 1.5540 - val_acc: 0.4412

Epoch 00003: val_loss did not improve from 1.42618
Epoch 4/80
898/897 [==============================] - 140s 156ms/step - loss: 1.3303 - acc: 0.5006 - val_loss: 1.4045 - val_acc: 0.4720

Epoch 00004: val_loss improved from 1.42618 to 1.40447, saving model to /Users/navyarao/Downloa


Epoch 00036: val_loss did not improve from 1.03650
Epoch 37/80
898/897 [==============================] - 146s 162ms/step - loss: 0.9872 - acc: 0.6319 - val_loss: 1.0406 - val_acc: 0.6145

Epoch 00037: val_loss did not improve from 1.03650
Epoch 38/80
898/897 [==============================] - 153s 170ms/step - loss: 0.9855 - acc: 0.6308 - val_loss: 1.0565 - val_acc: 0.6082

Epoch 00038: val_loss did not improve from 1.03650
Epoch 39/80
898/897 [==============================] - 154s 172ms/step - loss: 0.9874 - acc: 0.6316 - val_loss: 1.0498 - val_acc: 0.6149

Epoch 00039: val_loss did not improve from 1.03650
Epoch 40/80
898/897 [==============================] - 154s 172ms/step - loss: 0.9787 - acc: 0.6368 - val_loss: 1.1175 - val_acc: 0.5933

Epoch 00040: val_loss did not improve from 1.03650
Epoch 41/80
898/897 [==============================] - 154s 172ms/step - loss: 0.9743 - acc: 0.6361 - val_loss: 1.0348 - val_acc: 0.6204

Epoch 00041: val_loss improved from 1.03650 to 1.03476

898/897 [==============================] - 146s 163ms/step - loss: 0.8465 - acc: 0.6873 - val_loss: 0.9835 - val_acc: 0.6400

Epoch 00076: val_loss did not improve from 0.97166
Epoch 77/80
898/897 [==============================] - 144s 161ms/step - loss: 0.8476 - acc: 0.6851 - val_loss: 0.9782 - val_acc: 0.6406

Epoch 00077: val_loss did not improve from 0.97166
Epoch 78/80
898/897 [==============================] - 141s 157ms/step - loss: 0.8405 - acc: 0.6895 - val_loss: 0.9760 - val_acc: 0.6407

Epoch 00078: val_loss did not improve from 0.97166
Epoch 79/80
898/897 [==============================] - 147s 164ms/step - loss: 0.8397 - acc: 0.6909 - val_loss: 0.9799 - val_acc: 0.6417

Epoch 00079: val_loss did not improve from 0.97166
Epoch 80/80
898/897 [==============================] - 143s 160ms/step - loss: 0.8361 - acc: 0.6920 - val_loss: 0.9793 - val_acc: 0.6425

Epoch 00080: val_loss did not improve from 0.97166


In [14]:
from keras.preprocessing.image import img_to_array
from keras.models import load_model
import imutils
import cv2
import numpy as np
import sys

In [9]:
!pip install imutils

  Stored in directory: /Users/navyarao/Library/Caches/pip/wheels/16/84/1f/bf88641293cda2c8be81a5c4b8ca973dd9125a6dc3767417fd
Successfully built imutils


In [ ]:
from keras.preprocessing.image import img_to_array
import imutils
import cv2
from keras.models import load_model
import numpy as np

# parameters for loading data and images
detection_model_path = '/Users/navyarao/Downloads/FaceEmotion_ID-master/haarcascade_files/haarcascade_frontalface_default.xml'
emotion_model_path = '/Users/navyarao/Downloads/FaceEmotion_ID-master/models/_mini_XCEPTION.106-0.65.hdf5'


# hyper-parameters for bounding boxes shape
# loading models
face_detection = cv2.CascadeClassifier(detection_model_path)
emotion_classifier = load_model(emotion_model_path, compile=False)
EMOTIONS = ["angry" ,"disgust","scared", "happy", "sad", "surprised",
 "neutral"]


# starting video streaming
cv2.namedWindow('your_face')
camera = cv2.VideoCapture(0)
while True:
    frame = camera.read()[1]
    #reading the frame
    frame = imutils.resize(frame,width=400)
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    faces = face_detection.detectMultiScale(gray,scaleFactor=1.1,minNeighbors=5,minSize=(30,30),flags=cv2.CASCADE_SCALE_IMAGE)
    
    canvas = np.zeros((250, 300, 3), dtype="uint8")
    frameClone = frame.copy()
    if len(faces) > 0:
        faces = sorted(faces, reverse=True,
        key=lambda x: (x[2] - x[0]) * (x[3] - x[1]))[0]
        (fX, fY, fW, fH) = faces
                    # Extract the ROI of the face from the grayscale image, resize it to a fixed 48x48 pixels, and then prepare
            # the ROI for classification via the CNN
        roi = gray[fY:fY + fH, fX:fX + fW]
        roi = cv2.resize(roi, (48, 48))
        roi = roi.astype("float") / 255.0
        roi = img_to_array(roi)
        roi = np.expand_dims(roi, axis=0)
        print(roi)
        preds = emotion_classifier.predict(roi)[0]
        print(preds)
        emotion_probability = np.max(preds)
        label = EMOTIONS[preds.argmax()]

 
    for (i, (emotion, prob)) in enumerate(zip(EMOTIONS, preds)):
                # construct the label text
                text = "{}: {:.2f}%".format(emotion, prob * 100)
                w = int(prob * 300)
                cv2.rectangle(canvas, (7, (i * 35) + 5),
                (w, (i * 35) + 35), (0, 0, 255), -1)
                cv2.putText(canvas, text, (10, (i * 35) + 23),
                cv2.FONT_HERSHEY_SIMPLEX, 0.45,
                (255, 255, 255), 2)
                cv2.putText(frameClone, label, (fX, fY - 10),
                cv2.FONT_HERSHEY_SIMPLEX, 0.45, (0, 0, 255), 2)
                cv2.rectangle(frameClone, (fX, fY), (fX + fW, fY + fH),
                              (0, 0, 255), 2)

    cv2.imshow('your_face', frameClone)
    cv2.imshow("Probabilities", canvas)
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

camera.release()
cv2.destroyAllWindows()

[[[[0.4117647 ]
   [0.2901961 ]
   [0.32156864]
   ...
   [0.13333334]
   [0.22745098]
   [0.4627451 ]]

  [[0.43529412]
   [0.2784314 ]
   [0.3137255 ]
   ...
   [0.1254902 ]
   [0.18431373]
   [0.40392157]]

  [[0.42745098]
   [0.2784314 ]
   [0.30588236]
   ...
   [0.11764706]
   [0.16078432]
   [0.39607844]]

  ...

  [[0.12156863]
   [0.1764706 ]
   [0.13725491]
   ...
   [0.05490196]
   [0.07058824]
   [0.07450981]]

  [[0.11372549]
   [0.16078432]
   [0.16078432]
   ...
   [0.05490196]
   [0.05882353]
   [0.07843138]]

  [[0.11372549]
   [0.1254902 ]
   [0.14901961]
   ...
   [0.05490196]
   [0.06666667]
   [0.07058824]]]]
[1.93927139e-01 3.84551859e-05 2.48639192e-02 8.97190813e-03
 1.02140866e-01 2.66687223e-03 6.67390883e-01]
[[[[0.3254902 ]
   [0.28627452]
   [0.27450982]
   ...
   [0.15294118]
   [0.2901961 ]
   [0.50980395]]

  [[0.34509805]
   [0.28627452]
   [0.32941177]
   ...
   [0.13725491]
   [0.28235295]
   [0.4862745 ]]

  [[0.34509805]
   [0.26666668]
   [0.298039

[2.9004711e-01 6.6880260e-05 2.4530841e-02 1.6015757e-02 9.9243045e-02
 3.8900757e-03 5.6620628e-01]
[[[[0.33333334]
   [0.28235295]
   [0.27058825]
   ...
   [0.22745098]
   [0.44705883]
   [0.5882353 ]]

  [[0.34901962]
   [0.2784314 ]
   [0.31764707]
   ...
   [0.21176471]
   [0.49411765]
   [0.5568628 ]]

  [[0.33333334]
   [0.2901961 ]
   [0.32156864]
   ...
   [0.19215687]
   [0.40784314]
   [0.5372549 ]]

  ...

  [[0.1764706 ]
   [0.16078432]
   [0.09411765]
   ...
   [0.07058824]
   [0.07450981]
   [0.07843138]]

  [[0.15686275]
   [0.16862746]
   [0.10196079]
   ...
   [0.06666667]
   [0.07058824]
   [0.06666667]]

  [[0.12941177]
   [0.15294118]
   [0.1254902 ]
   ...
   [0.06666667]
   [0.07450981]
   [0.06666667]]]]
[2.0853814e-01 5.4516600e-05 1.8743243e-02 1.3722724e-02 7.6629318e-02
 1.9810395e-03 6.8033099e-01]
[[[[0.32941177]
   [0.2901961 ]
   [0.27450982]
   ...
   [0.15686275]
   [0.36862746]
   [0.57254905]]

  [[0.34901962]
   [0.2784314 ]
   [0.3137255 ]
   ...


[2.1291971e-01 7.4359232e-05 2.6107779e-02 1.3415008e-02 5.5154994e-02
 9.9953711e-03 6.8233275e-01]
[[[[0.2509804 ]
   [0.2901961 ]
   [0.31764707]
   ...
   [0.34901962]
   [0.54901963]
   [0.5921569 ]]

  [[0.25882354]
   [0.27450982]
   [0.2901961 ]
   ...
   [0.24313726]
   [0.47058824]
   [0.5568628 ]]

  [[0.24313726]
   [0.28627452]
   [0.28627452]
   ...
   [0.20392157]
   [0.39607844]
   [0.5529412 ]]

  ...

  [[0.16470589]
   [0.14509805]
   [0.13725491]
   ...
   [0.07058824]
   [0.07843138]
   [0.0627451 ]]

  [[0.14901961]
   [0.14901961]
   [0.12941177]
   ...
   [0.07058824]
   [0.07058824]
   [0.05098039]]

  [[0.14901961]
   [0.15686275]
   [0.13333334]
   ...
   [0.06666667]
   [0.06666667]
   [0.05490196]]]]
[2.1294516e-01 1.0477445e-04 2.8885756e-02 6.0680835e-03 8.5995711e-02
 1.1657321e-02 6.5434319e-01]
[[[[0.2784314 ]
   [0.29803923]
   [0.2784314 ]
   ...
   [0.32156864]
   [0.5058824 ]
   [0.5882353 ]]

  [[0.25882354]
   [0.3019608 ]
   [0.30980393]
   ...


[[[[0.3019608 ]
   [0.30588236]
   [0.2509804 ]
   ...
   [0.14509805]
   [0.4       ]
   [0.52156866]]

  [[0.2901961 ]
   [0.32941177]
   [0.27058825]
   ...
   [0.13333334]
   [0.28627452]
   [0.44705883]]

  [[0.3019608 ]
   [0.28627452]
   [0.28235295]
   ...
   [0.1254902 ]
   [0.21176471]
   [0.41960785]]

  ...

  [[0.16078432]
   [0.14901961]
   [0.16078432]
   ...
   [0.07058824]
   [0.08235294]
   [0.07058824]]

  [[0.16078432]
   [0.14901961]
   [0.13333334]
   ...
   [0.07450981]
   [0.07450981]
   [0.07058824]]

  [[0.15294118]
   [0.14117648]
   [0.13333334]
   ...
   [0.07058824]
   [0.07058824]
   [0.05882353]]]]
[1.8670864e-01 6.7887704e-05 2.6505554e-02 9.3881711e-03 6.7714073e-02
 4.4131246e-03 7.0520258e-01]
[[[[0.2901961 ]
   [0.30980393]
   [0.25882354]
   ...
   [0.14509805]
   [0.32156864]
   [0.49019608]]

  [[0.26666668]
   [0.31764707]
   [0.3137255 ]
   ...
   [0.12156863]
   [0.1764706 ]
   [0.42352942]]

  [[0.2901961 ]
   [0.2901961 ]
   [0.29411766]
   

[[[[0.40784314]
   [0.27058825]
   [0.3254902 ]
   ...
   [0.13333334]
   [0.18039216]
   [0.48235294]]

  [[0.3764706 ]
   [0.3529412 ]
   [0.34117648]
   ...
   [0.1254902 ]
   [0.14901961]
   [0.38431373]]

  [[0.33333334]
   [0.3137255 ]
   [0.34117648]
   ...
   [0.11372549]
   [0.13725491]
   [0.3372549 ]]

  ...

  [[0.12941177]
   [0.19215687]
   [0.1254902 ]
   ...
   [0.04705882]
   [0.06666667]
   [0.0627451 ]]

  [[0.11764706]
   [0.17254902]
   [0.14901961]
   ...
   [0.04705882]
   [0.06666667]
   [0.0627451 ]]

  [[0.10980392]
   [0.13333334]
   [0.15686275]
   ...
   [0.05098039]
   [0.05490196]
   [0.05882353]]]]
[2.3283641e-01 1.3467818e-04 2.5807116e-02 1.7958529e-02 1.4589879e-01
 1.8540454e-03 5.7551044e-01]
[[[[0.38431373]
   [0.3019608 ]
   [0.34509805]
   ...
   [0.12156863]
   [0.16078432]
   [0.28627452]]

  [[0.33333334]
   [0.34509805]
   [0.35686275]
   ...
   [0.11764706]
   [0.13725491]
   [0.26666668]]

  [[0.32941177]
   [0.30980393]
   [0.36862746]
   

...

[[[[0.85490197]
   [0.40392157]
   [0.20784314]
   ...
   [0.40784314]
   [0.4627451 ]
   [0.5254902 ]]

  [[0.8352941 ]
   [0.3372549 ]
   [0.19215687]
   ...
   [0.37254903]
   [0.4392157 ]
   [0.49411765]]

  [[0.7372549 ]
   [0.3372549 ]
   [0.1882353 ]
   ...
   [0.3529412 ]
   [0.41568628]
   [0.4745098 ]]

  ...

  [[0.84313726]
   [0.89411765]
   [0.76862746]
   ...
   [0.16862746]
   [0.23529412]
   [0.35686275]]

  [[0.76862746]
   [0.5647059 ]
   [0.42745098]
   ...
   [0.19215687]
   [0.20784314]
   [0.30588236]]

  [[0.30980393]
   [0.29411766]
   [0.25490198]
   ...
   [0.14117648]
   [0.16862746]
   [0.29803923]]]]
[2.31003821e-01 3.62754246e-04 1.14787005e-01 8.58637691e-02
 1.18931301e-01 7.02169072e-03 4.42029685e-01]
[[[[0.18039216]
   [0.14117648]
   [0.1254902 ]
   ...
   [0.3882353 ]
   [0.44313726]
   [0.53333336]]

  [[0.18431373]
   [0.13725491]
   [0.1254902 ]
   ...
   [0.36862746]
   [0.42352942]
   [0.4862745 ]]

  [[0.19215687]
   [0.14117648]
   [0.121568

[[[[0.74509805]
   [0.43137255]
   [0.22352941]
   ...
   [0.39215687]
   [0.43529412]
   [0.49411765]]

  [[0.7372549 ]
   [0.34117648]
   [0.19607843]
   ...
   [0.3529412 ]
   [0.4       ]
   [0.4627451 ]]

  [[0.654902  ]
   [0.3019608 ]
   [0.18431373]
   ...
   [0.3372549 ]
   [0.3764706 ]
   [0.43137255]]

  ...

  [[0.6156863 ]
   [0.5882353 ]
   [0.43529412]
   ...
   [0.15294118]
   [0.16078432]
   [0.2       ]]

  [[0.27450982]
   [0.27058825]
   [0.2784314 ]
   ...
   [0.12941177]
   [0.14509805]
   [0.1882353 ]]

  [[0.20392157]
   [0.21568628]
   [0.2627451 ]
   ...
   [0.12941177]
   [0.12941177]
   [0.16862746]]]]
[2.0505473e-01 1.2967136e-04 1.0457083e-01 1.0570792e-01 9.7399659e-02
 6.5520890e-03 4.8058510e-01]
[[[[0.70980394]
   [0.60784316]
   [0.24313726]
   ...
   [0.4117647 ]
   [0.4509804 ]
   [0.5019608 ]]

  [[0.7764706 ]
   [0.53333336]
   [0.19607843]
   ...
   [0.39215687]
   [0.43137255]
   [0.49411765]]

  [[0.6784314 ]
   [0.41568628]
   [0.19607843]
   

[[[[0.6901961 ]
   [0.7019608 ]
   [0.50980395]
   ...
   [0.40784314]
   [0.5137255 ]
   [0.6431373 ]]

  [[0.6745098 ]
   [0.6901961 ]
   [0.5568628 ]
   ...
   [0.3764706 ]
   [0.47843137]
   [0.60784316]]

  [[0.6784314 ]
   [0.68235296]
   [0.5137255 ]
   ...
   [0.3882353 ]
   [0.46666667]
   [0.56078434]]

  ...

  [[0.7411765 ]
   [0.77254903]
   [0.7137255 ]
   ...
   [0.19607843]
   [0.21960784]
   [0.2784314 ]]

  [[0.7372549 ]
   [0.76862746]
   [0.7058824 ]
   ...
   [0.18039216]
   [0.19607843]
   [0.2509804 ]]

  [[0.7294118 ]
   [0.75686276]
   [0.70980394]
   ...
   [0.14901961]
   [0.18039216]
   [0.23921569]]]]
[1.8760403e-01 2.6911785e-04 1.4582606e-01 6.2674835e-02 1.2216044e-01
 7.9977270e-03 4.7346774e-01]
[[[[0.6784314 ]
   [0.6745098 ]
   [0.39607844]
   ...
   [0.5019608 ]
   [0.627451  ]
   [0.7411765 ]]

  [[0.6666667 ]
   [0.6862745 ]
   [0.34117648]
   ...
   [0.4745098 ]
   [0.5764706 ]
   [0.7058824 ]]

  [[0.6666667 ]
   [0.654902  ]
   [0.30980393]
   

[[[[0.12941177]
   [0.13333334]
   [0.10588235]
   ...
   [0.6117647 ]
   [0.7411765 ]
   [1.        ]]

  [[0.13333334]
   [0.10980392]
   [0.10196079]
   ...
   [0.5921569 ]
   [0.6784314 ]
   [1.        ]]

  [[0.15294118]
   [0.11764706]
   [0.08627451]
   ...
   [0.5411765 ]
   [0.63529414]
   [0.99215686]]

  ...

  [[0.7176471 ]
   [0.7294118 ]
   [0.7411765 ]
   ...
   [0.58431375]
   [0.87058824]
   [1.        ]]

  [[0.7137255 ]
   [0.72156864]
   [0.7372549 ]
   ...
   [0.50980395]
   [0.7372549 ]
   [0.972549  ]]

  [[0.7137255 ]
   [0.7254902 ]
   [0.74509805]
   ...
   [0.46666667]
   [0.67058825]
   [0.6666667 ]]]]
[1.2975079e-01 4.3290254e-04 9.9126339e-02 8.2396060e-02 1.1749356e-01
 1.3491609e-02 5.5730885e-01]
[[[[0.09411765]
   [0.09019608]
   [0.09803922]
   ...
   [0.5411765 ]
   [0.54509807]
   [0.64705884]]

  [[0.08235294]
   [0.08235294]
   [0.08627451]
   ...
   [0.5058824 ]
   [0.52156866]
   [0.6039216 ]]

  [[0.09411765]
   [0.08627451]
   [0.08235294]
   

[[[[0.45882353]
   [0.15294118]
   [0.12941177]
   ...
   [0.5372549 ]
   [0.6117647 ]
   [0.7411765 ]]

  [[0.42352942]
   [0.15294118]
   [0.12941177]
   ...
   [0.5254902 ]
   [0.59607846]
   [0.73333335]]

  [[0.38431373]
   [0.13333334]
   [0.13333334]
   ...
   [0.49411765]
   [0.5921569 ]
   [0.7294118 ]]

  ...

  [[0.11764706]
   [0.13725491]
   [0.10196079]
   ...
   [0.6392157 ]
   [0.67058825]
   [0.64705884]]

  [[0.11764706]
   [0.11372549]
   [0.10196079]
   ...
   [0.3372549 ]
   [0.40784314]
   [0.46666667]]

  [[0.11764706]
   [0.10980392]
   [0.10980392]
   ...
   [0.20784314]
   [0.21568628]
   [0.20784314]]]]
[6.7864865e-02 1.1455648e-04 5.7318162e-02 3.1995200e-02 8.9222401e-02
 5.9228446e-03 7.4756193e-01]
[[[[0.34901962]
   [0.15686275]
   [0.1254902 ]
   ...
   [0.45490196]
   [0.6039216 ]
   [0.6313726 ]]

  [[0.33333334]
   [0.14509805]
   [0.1254902 ]
   ...
   [0.42745098]
   [0.56078434]
   [0.6156863 ]]

  [[0.2901961 ]
   [0.13333334]
   [0.14117648]
   